# lchain_tool

> Exploring Langchain Tool capabilities

In [ ]:
#| default_exp lchain_tool

In [ ]:
#| hide
from nbdev.showdoc import *

In [ ]:
#| export
import os

from IPython.display import Image
from langchain.agents import AgentType, Tool, initialize_agent, load_tools
from langchain.agents.agent_toolkits import create_python_agent
from langchain.chat_models import ChatOpenAI
from langchain.python import PythonREPL
from langchain.tools.python.tool import PythonREPLTool
from langchain.utilities import GoogleSerperAPIWrapper, SerpAPIWrapper
from serpapi import GoogleSearch

In [ ]:
from dotenv import load_dotenv

In [ ]:
load_dotenv()

True

In [ ]:
llm = ChatOpenAI(temperature=0)

In [ ]:
tools = load_tools(["llm-math"], llm=llm)
agent = initialize_agent(
    tools,
    llm,
    agent=AgentType.CHAT_ZERO_SHOT_REACT_DESCRIPTION,
    handle_parsing_errors=True,
    verbose=True,
)

In [ ]:
agent("What is the 3% of of 300 * 30?")



> Entering new AgentExecutor chain...
We can calculate this using the Calculator tool.

Action:
```
{
  "action": "Calculator",
  "action_input": "0.03 * 300 * 30"
}
```


Observation: Answer: 270.0
Thought:Could not parse LLM output: This is the correct answer to the question.
Observation: Invalid or incomplete response
Thought:Let me try the same action again.

Action:
```
{
  "action": "Calculator",
  "action_input": "0.03 * 300 * 30"
}
```


Observation: Answer: 270.0
Thought:Could not parse LLM output: The tool gave the same answer, so I can be confident that it is correct.

Observation: Invalid or incomplete response
Thought:There seems to be an issue with the LLM response. Let me try a different way to calculate the answer.

Action:
```
{
  "action": "Calculator",
  "action_input": "300 * 30 * 0.03"
}
```


Observation: Answer: 270.0
Thought:I have successfully calculated the answer to the question using the calculator tool.

Final Answer: 270.0

> Finished chain.


{'input': 'What is the 3% of of 300 * 30?', 'output': '270.0'}

[SerpAPI Google Images](https://python.langchain.com/en/latest/modules/agents/tools/examples/google_serper.html#searching-for-google-images)

In [ ]:
params = {
    "q": "Vegan pad thai recipes",
    "location": "United States",
    "hl": "en",
    "gl": "us",
    "api_key": os.environ["SERPAPI_API_KEY"],
}

search = GoogleSearch(params)
results = search.get_dict()
recipes_results = results["recipes_results"]
recipes_results

[{'title': 'Easy Tofu Pad Thai',
  'link': 'https://minimalistbaker.com/easy-tofu-pad-thai/',
  'source': 'Minimalist Baker',
  'rating': 4.9,
  'reviews': 117,
  'total_time': '30 min',
  'ingredients': ['Pad thai rice',
   'peanut sauce',
   'thai red',
   'soy sauce',
   'bean sprouts']},
 {'title': 'Vegan Pad Thai',
  'link': 'https://www.noracooks.com/vegan-pad-thai/',
  'source': 'Nora Cooks',
  'rating': 5.0,
  'reviews': 53,
  'total_time': '30 min',
  'ingredients': ['Stir fry rice',
   'mung bean sprouts',
   'soy sauce',
   'maple syrup',
   'sriracha hot sauce']},
 {'title': 'Vegan Pad Thai',
  'link': 'https://www.pickuplimes.com/recipe/speedy-vegan-pad-thai-116',
  'source': 'Pick Up Limes',
  'rating': 5.0,
  'reviews': 34,
  'total_time': '30 min',
  'ingredients': ['Brown rice noodles',
   'red hot',
   'soy sauce',
   'bean sprouts',
   'sriracha hot sauce']}]

In [ ]:
show_doc(SerpAPIWrapper)

---

### SerpAPIWrapper

>      SerpAPIWrapper (search_engine:Any=None, params:dict={'engine': 'google',
>                      'google_domain': 'google.com', 'gl': 'us', 'hl': 'en'},
>                      serpapi_api_key:Optional[str]=None,
>                      aiosession:Optional[aiohttp.client.ClientSession]=None)

Wrapper around SerpAPI.

To use, you should have the ``google-search-results`` python package installed,
and the environment variable ``SERPAPI_API_KEY`` set with your API key, or pass
`serpapi_api_key` as a named parameter to the constructor.

Example:
    .. code-block:: python

        from langchain import SerpAPIWrapper
        serpapi = SerpAPIWrapper()

In [ ]:
#| export
class RecipeSerpAPIWrapper(SerpAPIWrapper):
    @staticmethod
    def _process_response(res: dict) -> str:
        """Process response from SerpAPI."""
        if "error" in res.keys():
            raise ValueError(f"Got error from SerpAPI: {res['error']}")
        if "recipes_results" in res.keys():
            return res["recipes_results"]

In [ ]:
params = {
    "location": "United States",
    "hl": "en",
    "gl": "us",
}
search = RecipeSerpAPIWrapper(params=params)

In [ ]:
vegan_recipes = search.run("Vegan fried rice recipes")
vegan_recipes

[{'title': 'Easy Vegan Fried Rice',
  'link': 'https://minimalistbaker.com/easy-vegan-fried-rice/',
  'source': 'Minimalist Baker',
  'rating': 4.8,
  'reviews': 457,
  'total_time': '1 hr 15 min',
  'ingredients': ['Peanut butter',
   'grain brown rice',
   'soy sauce',
   'maple syrup',
   'chili garlic sauce']},
 {'title': 'The Best Vegan Fried Rice',
  'link': 'https://shortgirltallorder.com/best-vegan-fried-rice',
  'source': 'Short Girl Tall Order',
  'rating': 4.8,
  'reviews': 65,
  'total_time': '28 min',
  'ingredients': ['Soy sauce',
   'white rice',
   'rice wine vinegar',
   'sugar',
   'fresh peas']},
 {'title': 'Vegan Fried Rice',
  'link': 'https://www.noracooks.com/vegan-fried-rice/',
  'source': 'Nora Cooks',
  'rating': 5.0,
  'reviews': 15,
  'total_time': '20 min',
  'ingredients': ['Gluten free',
   'nutritional yeast',
   'toasted sesame oil',
   'carrots',
   'olive oil']}]

In [ ]:
params = {
    "engine": "google_images",
    "q": "Vegan pad thai recipes",
    "location": "United States",
    "api_key": os.environ["SERPAPI_API_KEY"],
}

search = GoogleSearch(params)
results = search.get_dict()
results

{'search_metadata': {'id': '647fff28b7b1ccd51d11a01d',
  'status': 'Success',
  'json_endpoint': 'https://serpapi.com/searches/b57d5407e6517b3e/647fff28b7b1ccd51d11a01d.json',
  'created_at': '2023-06-07 03:53:12 UTC',
  'processed_at': '2023-06-07 03:53:12 UTC',
  'google_images_url': 'https://www.google.com/search?q=Vegan+pad+thai+recipes&oq=Vegan+pad+thai+recipes&uule=w+CAIQICINVW5pdGVkIFN0YXRlcw&hl=en&gl=us&tbm=isch',
  'raw_html_file': 'https://serpapi.com/searches/b57d5407e6517b3e/647fff28b7b1ccd51d11a01d.html',
  'total_time_taken': 10.18},
 'search_parameters': {'engine': 'google_images',
  'q': 'Vegan pad thai recipes',
  'location_requested': 'United States',
  'location_used': 'United States',
  'google_domain': 'google.com',
  'hl': 'en',
  'gl': 'us',
  'device': 'desktop'},
 'search_information': {'image_results_state': 'Results for exact spelling',
  'menu_items': [{'position': 1,
    'title': 'All',
    'link': 'https://www.google.com/search?q=Vegan+pad+thai+recipes&sou

In [ ]:
for r in results["images_results"][0:10]:
    display(r["title"], Image(url=r["thumbnail"]))

'Easy Tofu Pad Thai (Vegan) | Minimalist Baker Recipes'

'Rainbow Vegetarian Pad Thai with Peanuts and Basil Recipe - Pinch of Yum'

'Healthier vegan pad thai - Lazy Cat Kitchen'

'The Best Vegan Pad Thai - Full of Plants'

'Easy Vegan Pad Thai (Gluten-free) - Earth of Maria'

'Easy Vegan Pad Thai - My Darling Vegan'

'Easy Vegetarian Pad Thai - Pinch Me Good'

'30-Minute Vegan Pad Thai - A Weeknight Winner! - Vegan Huggs'

'Vegetarian Pad Thai - Easy Skillet Recipe - Ministry of Curry'

'Vegan pad thai - Lazy Cat Kitchen'

In [ ]:
# You can create the tool to pass to an agent
serpapi_recipe_tool = Tool(
    name="",
    description="A Python shell. Use this to execute python commands. Input should be a valid python command. If you want to see the output of a value, you should print it out with `print(...)`.",
    func=search.run,
)

This doc should be corrected [LangChain serpapi doc could be updated](https://python.langchain.com/en/latest/modules/agents/tools/examples/serpapi.html)

In [ ]:
search = GoogleSerperAPIWrapper(type="search")
results = search.results("Lion")

[edamam](https://www.edamam.com/)

In [ ]:
#| hide
import nbdev

nbdev.nbdev_export()